# gpCAM Test Notebook
In this notebook we will go through many features of gpCAM. Work through it 
and you are ready for your own autonomous experiment. 

## This first cell has nothing to do with gpCAM, it's just a function to plot some results later

In [9]:
import plotly.graph_objects as go
import numpy as np
def plot(x,y,z,data = None):
    fig = go.Figure()
    fig.add_trace(go.Surface(x = x, y = y,z=z))
    if data is not None: 
        fig.add_trace(go.Scatter3d(x=data[:,0], y=data[:,1], z=data[:,2],
                                   mode='markers'))

    fig.update_layout(title='Posterior Mean', autosize=True,
                  width=800, height=800,
                  margin=dict(l=65, r=50, b=65, t=90))


    fig.show()

## Here we want to define some points at which we will predict, still has nothing to do with gpCAM 

In [10]:
x_pred = np.zeros((10000,2))
x = np.linspace(0,10,100)
y = np.linspace(0,10,100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.array([x[i,j],y[i,j]])
        counter += 1

## Let's get after it by setting up a Single-Task GP Autonomous Data Acquisition Run

In [11]:
def optional_acq_func(x,obj):
    #this acquisition function makes the autonomous experiment a Bayesian optimization
    a = 3.0 #3.0 for 95 percent confidence interval
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    return mean + a * cov

def optional_mean_func(gp_obj,x,hyperparameters):
    return ((x[:,0] ** 2 + x[:,1] - 11.0) ** 2 + (x[:,0] + x[:,1] ** 2 - 7.0) ** 2) * hyperparameters[-1]

def optional_cost_function(origin,x,arguments = None):
    #cost pf l1 motion in the input space
    offset = arguments["offset"]
    slope = arguments["slope"]
    d = np.abs(np.subtract(origin,x))
    c = (d * slope) + offset
    n = np.sum(c)
    return n
def optional_cost_update_function(costs, parameters):
    ###defining a cost update function might look tricky but just need a bit
    ###of tenacity. And remember, this is optional, if you have a great guess for your costs you
    ###don't need to update the costs. Also, if you don't account for costs, this funciton is not needed
    from scipy.optimize import differential_evolution as devo
    print("Cost adjustment in progress...")
    print("old cost parameters: ",parameters)
    bounds = np.array([[0.001,10],[0.0001,10]])
    ###remove outliers:
    origins = []
    points = []
    motions = []
    c   = []
    cost_per_motion = []
    for i in range(len(costs)):
        origins.append(costs[i][0])
        points.append(costs[i][1])
        motions.append(abs(costs[i][0] - costs[i][1]))
        c.append(costs[i][2])
        cost_per_motion.append(costs[i][2]/optional_cost_function(costs[i][0],costs[i][1], parameters))
    mean_costs_per_distance = np.mean(np.asarray(cost_per_motion))
    sd = np.std(np.asarray(cost_per_motion))
    for element in cost_per_motion:
        if (
            element >= mean_costs_per_distance - 2.0 * sd
            and element <= mean_costs_per_distance + 2.0 * sd
        ):
            continue
        else:
            motions.pop(cost_per_motion.index(element))
            c.pop(cost_per_motion.index(element))
            origins.pop(cost_per_motion.index(element))
            points.pop(cost_per_motion.index(element))
            cost_per_motion.pop(cost_per_motion.index(element))
    def compute_l1_cost_misfit(params, origins,points, costs):
        parameters = {"offset": params[0], "slope": params[1]}
        sum1 = 0.0
        for idx in range(len(points)):
            sum1 = sum1 + (
                (optional_cost_function(origins[idx],points[idx],parameters) - costs[idx]) ** 2)
        return sum1
    res = devo(compute_l1_cost_misfit, bounds, args = (origins, points,c), tol=1e-6, disp=True, maxiter=300, popsize=20,polish=False)
    arguments = {"offset": res["x"][0],"slope": res["x"][1:]}
    print("New cost parameters: ", arguments)
    return arguments

In [12]:
import time
from gpcam.autonomous_experimenter import AutonomousExperimenterGP

def instrument(data):
    for entry in data:
        entry["value"] = np.sin(np.linalg.norm(entry["position"]))
        #entry["cost"]  = [np.array([0,0]),entry["position"],np.sum(entry["position"])]
    return data
#initialization
#feel free to try different acquisition functions, e.g. optional_acq_func, "covariance", "shannon_ig"
#note how costs are defined in for the autonomous experimenter
my_ae = AutonomousExperimenterGP(np.array([[0,10],[0,10]]),instrument,
                                 np.ones((3)),np.array([[0.001,100],[0.001,100],[0.001,100]]),
                                 init_dataset_size= 20, 
                                 acq_func = "covariance", #optional_acq_func, 
                                 #cost_func = optional_cost_function, 
                                 #cost_update_func = optional_cost_update_function,
                                 cost_func_params={"offset": 5.0,"slope":10.0}, 
                                  kernel_func = None)#, prior_mean_func = optional_mean_func)


print("length of the dataset: ",len(my_ae.x))

#training
import time
start_time = time.time()
my_ae.train_async(max_iter = 2) #train asynchronously
my_ae.opt_obj.get_final()
end_time = time.time()
print(end_time - start_time)
#my_ae.train()       #or not
#print("Initial training submitted")
#for i in range(2): #this loop shows how hyperparameters are changing if they are trained asynchronously
#    time.sleep(2)
#     my_ae.update_hps()
#my_ae.train_async()
#my_ae.update_hps()

New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
Costs successfully initialized
##################################################################################
Initialization successfully concluded
now train(...) or train_async(...), and then go(...)
##################################################################################
length of the dataset:  20
Async fvGP training started with  20  data points
fvGP submitted HGDL optimization for asynchronous training
bounds: [[1.e-03 1.e+02]
 [1.e-03 1.e+02]
 [1.e-03 1.e+02]]
deflation radius:  None
HGDL successfully initiated
deflation radius set to  0.09999899999999999
Host  tcp://127.0.0.1:33211  has  3  workers.
<Client: 'tcp://127.0.0.1:35937' processes=4 threads=16, memory=31.30 GiB>
HGDL starts with:  [[ 1.          1.          1.        ]
 [61.50539755 63.98114597 98.74747049]
 [ 0.33863364 51.08826002  9.65541745

In [13]:
my_ae.kill_client()

fvGP is killing asynchronous training....
HGDL kill client initialized ...
HGDL kill client successful
fvGP successfully killed the training.


## Let's see what our initial model looks like

In [14]:
f = my_ae.gp_optimizer.posterior_mean(x_pred)["f(x)"]
f_re = f.reshape(100,100)

plot(x,y,f_re, data = np.column_stack([my_ae.x,my_ae.y]))

## Let's run the autonomus loop to 100 points

In [15]:
help(my_ae.go)

Help on method go in module gpcam.autonomous_experimenter:

go(N=1000000000000000.0, breaking_error=1e-50, retrain_globally_at=[100, 400, 1000], retrain_locally_at=[20, 40, 60, 80, 100, 200, 400, 1000], retrain_async_at=[1000, 2000, 5000, 10000], retrain_callable_at=[], update_cost_func_at=[], acq_func_opt_setting=<function AutonomousExperimenterGP.<lambda> at 0x7fe4970ba820>, training_opt_callable=None, training_opt_max_iter=20, training_opt_pop_size=10, training_opt_tol=1e-06, acq_func_opt_max_iter=20, acq_func_opt_pop_size=20, acq_func_opt_tol=1e-06, acq_func_opt_tol_adjust=[True, 0.1], number_of_suggested_measurements=1) method of gpcam.autonomous_experimenter.AutonomousExperimenterGP instance
    function to start the autonomous-data-acquisition loop
    optional parameters:
    -----------
        * N = 1e15 ... run N iterations
        * breaking_error = 1e-15 ... run until breaking_error is achieved
        * retrain_globally_at = [100,400,1000]
        * retrain_locally_at = [

In [16]:
#run the loop
my_ae.go(N = 100, 
            retrain_async_at=[],
            retrain_globally_at = [],
            retrain_locally_at = [],
            acq_func_opt_setting = lambda number: "global" if number % 2 == 0 else "local",
            training_opt_callable = None,
            training_opt_max_iter = 20,
            training_opt_pop_size = 10,
            training_opt_tol      = 1e-6,
            acq_func_opt_max_iter = 20,
            acq_func_opt_pop_size = 20,
            acq_func_opt_tol      = 1e-6,
            acq_func_opt_tol_adjust = [True,0.1])#,update_cost_func_at = [30])
print("length of the dataset is now: ", len(my_ae.x))
#and that runs the autonomous loop

Date and time:        2021-07-27_16_50_51



iteration:  20
Run Time:  0.00022459030151367188      seconds
Number of measurements:  20
hps:  [1. 1. 1.]
ask() initiated with hyperparameters: [1. 1. 1.]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  1e-06
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters:  {'offset': 5.0, 'slope': 10.0}
differential_evolution step 1: f(x)= -0.999529
differential_evolution step 2: f(x)= -0.999551
differential_evolution step 3: f(x)= -0.999715
differential_evolution step 4: f(x)= -0.999715
differential_evolution step 5: f(x)= -0.999715
differential_evolution step 6: f(x)= -0.999715
differential_evolution step 7: f(x)= -0.999765
differential_evolution step 8: f(x)= -0.999803
differential_evolution step 9: f(x)= -0.999803
differential_evolution step 10: f(x)= -0.999803
differential_evolution step 11: f(x)= -0.999807
differentia

hps:  [0.50180205 2.45197311 2.90933179]
ask() initiated with hyperparameters: [0.50180205 2.45197311 2.90933179]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  0.04613548205723622
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters:  {'offset': 5.0, 'slope': 10.0}
differential_evolution step 1: f(x)= -0.581419
differential_evolution step 2: f(x)= -0.581419
differential_evolution step 3: f(x)= -0.581419
differential_evolution step 4: f(x)= -0.596132
differential_evolution step 5: f(x)= -0.596132
differential_evolution step 6: f(x)= -0.596521
differential_evolution step 7: f(x)= -0.597737
The acquisition function optimization resulted in: 
     x:  [[6.96557362 9.92404487]]
  f(x):  [-0.59773724]
acquisition funciton optimization tolerance changed to:  0.05977372444470652
Next points to be requested: 
[[6.96557362 9.92404487]]
Sending request to instrument .

differential_evolution step 3: f(x)= -0.521825
differential_evolution step 4: f(x)= -0.53035
The acquisition function optimization resulted in: 
     x:  [[1.59840731 0.09447943]]
  f(x):  [-0.53034983]
acquisition funciton optimization tolerance changed to:  0.05303498313754315
Next points to be requested: 
[[1.59840731 0.09447943]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.50180205 2.45197311 2.90933179]
The GPOptimizer updated the Hyperperameters:  [0.50180205 2.45197311 2.90933179]
The Autonomus Experimenter

acquisition funciton optimization tolerance changed to:  0.04980661356955643
Next points to be requested: 
[[8.79354021 9.95000237]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.50180205 2.45197311 2.90933179]
The GPOptimizer updated the Hyperperameters:  [0.50180205 2.45197311 2.90933179]
The Autonomus Experimenter updated the hyperparameters
hps:  [0.50180205 2.45197311 2.90933179]



iteration:  41
Run Time:  1.2447257041931152      seconds
Number of measurements:  41
hps:  [0.50180205 2.45197311 2.90933179]
ask

differential_evolution step 8: f(x)= -0.479481
differential_evolution step 9: f(x)= -0.479481
The acquisition function optimization resulted in: 
     x:  [[9.84716982 8.47849682]]
  f(x):  [-0.47948139]
acquisition funciton optimization tolerance changed to:  0.047948138766208195
Next points to be requested: 
[[9.84716982 8.47849682]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.50180205 2.45197311 2.90933179]
The GPOptimizer updated the Hyperperameters:  [0.50180205 2.45197311 2.90933179]
The Autonomus Experiment

...

differential_evolution step 2: f(x)= -0.428043
differential_evolution step 3: f(x)= -0.428043
differential_evolution step 4: f(x)= -0.428043
differential_evolution step 5: f(x)= -0.430714
differential_evolution step 6: f(x)= -0.440811
differential_evolution step 7: f(x)= -0.440811
differential_evolution step 8: f(x)= -0.448288
differential_evolution step 9: f(x)= -0.448288
differential_evolution step 10: f(x)= -0.451453
differential_evolution step 11: f(x)= -0.451453
differential_evolution step 12: f(x)= -0.451453
differential_evolution step 13: f(x)= -0.451738
differential_evolution step 14: f(x)= -0.451738
The acquisition function optimization resulted in: 
     x:  [[6.70509745e+00 6.15775322e-03]]
  f(x):  [-0.45173765]
acquisition funciton optimization tolerance changed to:  0.045173765272794465
Next points to be requested: 
[[6.70509745e+00 6.15775322e-03]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data com

done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.50180205 2.45197311 2.90933179]
The GPOptimizer updated the Hyperperameters:  [0.50180205 2.45197311 2.90933179]
The Autonomus Experimenter updated the hyperparameters
hps:  [0.50180205 2.45197311 2.90933179]



iteration:  81
Run Time:  3.685230255126953      seconds
Number of measurements:  81
hps:  [0.50180205 2.45197311 2.90933179]
ask() initiated with hyperparameters: [0.50180205 2.45197311 2.90933179]
optimization method:  local
bounds:  None
finding acquisition function maxima...
optimization method  local
tolerance:  0.04126375037453776
po

    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.50180205 2.45197311 2.90933179]
The GPOptimizer updated the Hyperperameters:  [0.50180205 2.45197311 2.90933179]
The Autonomus Experimenter updated the hyperparameters
hps:  [0.50180205 2.45197311 2.90933179]



iteration:  86
Run Time:  4.095776796340942      seconds
Number of measurements:  86
hps:  [0.50180205 2.45197311 2.90933179]
ask() initiated with hyperparameters: [0.50180205 2.45197311 2.90933179]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  0.03166122789725817
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters:  {'offset': 5.0, 'slope': 10.0}
differential_evolution step 1: f(x)= -0.4

differential_evolution step 2: f(x)= -0.389061
differential_evolution step 3: f(x)= -0.39205
differential_evolution step 4: f(x)= -0.39205
differential_evolution step 5: f(x)= -0.393961
differential_evolution step 6: f(x)= -0.399949
The acquisition function optimization resulted in: 
     x:  [[1.3526545 9.8843867]]
  f(x):  [-0.39994892]
acquisition funciton optimization tolerance changed to:  0.03999489211535702
Next points to be requested: 
[[1.3526545 9.8843867]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.501

[[9.26570262 7.36879441]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
Updating the hyperparameters in fvGP...
    fvGP async hyperparameter update successful
    Latest hyperparameters:  [0.50180205 2.45197311 2.90933179]
The GPOptimizer updated the Hyperperameters:  [0.50180205 2.45197311 2.90933179]
The Autonomus Experimenter updated the hyperparameters
hps:  [0.50180205 2.45197311 2.90933179]



iteration:  97
Run Time:  4.905113220214844      seconds
Number of measurements:  97
hps:  [0.50180205 2.45197311 2.90933179]
ask() initiated with hyperparameters: [0.50180205 2.45197311 2.90933179]
optimization method:  local
bounds:  N






## Now let's plot the posterior mean after the experiment has concluded

In [17]:
res = my_ae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f, data = np.column_stack([my_ae.x,my_ae.y]))

## Running a Multi-Task GP Autonomous Data Acquisition
This example uses 21 (!) dim robot data and 7 tasks, which you can all use or pick a subset of them

In [18]:
##prepare some data
import numpy as np
from scipy.interpolate import griddata
data = np.load("sarcos.npy")
print(data.shape)
x = data[:,0:21]
y = data[:,21:23]

(4449, 28)


In [19]:
from gpcam.autonomous_experimenter import AutonomousExperimenterFvGP


def instrument(data):
    for entry in data:
        entry["values"] = griddata(x,y,entry["position"],method = "nearest", fill_value = 0)[0]
        entry["value positions"] = np.array([[0],[1]])
    return data

input_s = np.array([np.array([np.min(x[:,i]),np.max(x[:,i])]) for i in range(len(x[0]))])
print("index set (input space) bounds:")
print(input_s)
print("hps bounds:")
hps_bounds = np.empty((22,2))
hps_bounds[:,0] = 0.0001
hps_bounds[:,1] = 100.0
hps_bounds[0] = np.array([0.0001, 10000])
print(hps_bounds)
print("shape of y: ")
print(y.shape)

my_fvae = AutonomousExperimenterFvGP(input_s,2,1,instrument,np.ones((22)),hps_bounds,
                                     init_dataset_size= 10)
my_fvae.train()
my_fvae.go(N = 100)

index set (input space) bounds:
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
hps bounds:
[[1.e-04 1.e+04]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]]
shape of y: 
(4449, 2)
CAUTION: fvGP reports that you h

differential_evolution step 1: f(x)= -15.6031
The acquisition function optimization resulted in: 
     x:  [[ -0.61094234  -0.74179245   0.27035507   0.80713384   1.01245823
   -0.90729942   0.13623824  -2.94577494   2.03306908  -1.28439515
    0.36759724   0.46592868   0.2605795    0.14723571 -46.45411255
   16.13216429 -22.36192155  67.20876561  34.92041342 -11.70052604
    3.88480188]]
  f(x):  [-15.6031432]
acquisition funciton optimization tolerance changed to:  1.5603143202847247
Next points to be requested: 
[[ -0.61094234  -0.74179245   0.27035507   0.80713384   1.01245823
   -0.90729942   0.13623824  -2.94577494   2.03306908  -1.28439515
    0.36759724   0.46592868   0.2605795    0.14723571 -46.45411255
   16.13216429 -22.36192155  67.20876561  34.92041342 -11.70052604
    3.88480188]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++

differential_evolution step 1: f(x)= -15.3115
The acquisition function optimization resulted in: 
     x:  [[  0.43515916  -0.35712506  -0.1546507    2.07253738   0.15225301
   -0.20926237  -0.18986674   0.08576429   0.57020345  -1.10665706
   -2.51780839  -2.2507298    0.92782315  -2.24430787  34.94333435
   24.34375784 -24.35636498 -35.25274305  33.70712708  12.76754363
    2.56738441]]
  f(x):  [-15.31149507]
acquisition funciton optimization tolerance changed to:  1.5311495068250982
Next points to be requested: 
[[  0.43515916  -0.35712506  -0.1546507    2.07253738   0.15225301
   -0.20926237  -0.18986674   0.08576429   0.57020345  -1.10665706
   -2.51780839  -2.2507298    0.92782315  -2.24430787  34.94333435
   24.34375784 -24.35636498 -35.25274305  33.70712708  12.76754363
    2.56738441]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++

differential_evolution step 1: f(x)= -14.7703
The acquisition function optimization resulted in: 
     x:  [[-3.89125393e-01 -1.43418653e-01  2.52546253e-02  1.45057065e+00
   2.57732796e-01 -1.69749584e-01  5.50249367e-01 -3.63471383e+00
   5.28494709e-01  1.45183378e+00 -2.59172539e+00  7.99854377e-01
   1.14682511e+00 -1.90057212e+00  2.68149343e+01 -1.31327869e+01
  -2.27329309e+01  6.58942496e+01  2.61624749e+01 -1.22859487e+00
   2.77077882e+01]]
  f(x):  [-14.77028836]
acquisition funciton optimization tolerance changed to:  1.4770288356653356
Next points to be requested: 
[[-3.89125393e-01 -1.43418653e-01  2.52546253e-02  1.45057065e+00
   2.57732796e-01 -1.69749584e-01  5.50249367e-01 -3.63471383e+00
   5.28494709e-01  1.45183378e+00 -2.59172539e+00  7.99854377e-01
   1.14682511e+00 -1.90057212e+00  2.68149343e+01 -1.31327869e+01
  -2.27329309e+01  6.58942496e+01  2.61624749e+01 -1.22859487e+00
   2.77077882e+01]]
Sending request to instrument ...
Data received
Checking if dat

differential_evolution step 1: f(x)= -14.8215
The acquisition function optimization resulted in: 
     x:  [[  0.56867243  -0.3192441   -0.16899284   1.66983959   0.16080581
   -0.34180202   0.63106679  -0.71235051   0.34748272  -2.76951392
   -2.42481038  -1.50044932  -1.13600062   0.86833638  -0.56534557
   16.24472254  21.93161905  70.96049645 -35.53627083 -19.17892812
   18.78919946]]
  f(x):  [-14.82147384]
acquisition funciton optimization tolerance changed to:  1.4821473839956267
Next points to be requested: 
[[  0.56867243  -0.3192441   -0.16899284   1.66983959   0.16080581
   -0.34180202   0.63106679  -0.71235051   0.34748272  -2.76951392
   -2.42481038  -1.50044932  -1.13600062   0.86833638  -0.56534557
   16.24472254  21.93161905  70.96049645 -35.53627083 -19.17892812
   18.78919946]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++

...

differential_evolution step 1: f(x)= -13.4407
The acquisition function optimization resulted in: 
     x:  [[  0.63713662  -0.47171646   0.20482028   1.19387146  -0.11087134
   -0.36254925   0.41169242   3.60591383  -1.53071537  -1.95460647
    2.19335047  -1.69138905   0.74016565   1.81564307  40.98389043
   21.6537115   25.1349964   64.31212919  28.18258923 -19.14561075
  -29.20855919]]
  f(x):  [-13.44065171]
acquisition funciton optimization tolerance changed to:  1.3440651706699327
Next points to be requested: 
[[  0.63713662  -0.47171646   0.20482028   1.19387146  -0.11087134
   -0.36254925   0.41169242   3.60591383  -1.53071537  -1.95460647
    2.19335047  -1.69138905   0.74016565   1.81564307  40.98389043
   21.6537115   25.1349964   64.31212919  28.18258923 -19.14561075
  -29.20855919]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The Autonomous Experimenter is trying to update the hyperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [274.93737689  34.80918858   6.19882684  34.87816902  92.75477355
  66.21239747  65.49201439  86.7399635   49.22794349  33.82484656
  42.4306653   42.06139673  73.76188949  70.75553502  79.41519322
  18.3599238   77.63851134  33.93650471  99.80399254  91.77096741
  78.90337852  94.62295295]



iteration:  90
Run Time:  31.3272807598114      seconds
Number of measurements:  90
hps:  [274.93737689  34.80918858   6.19882684  34.87816902  92.75477355
  66.21239747  65.49201439  86.7399635   49.22794349  33.82484656
  42.4306653   42.06139673  73.76188949  70.75553502

differential_evolution step 1: f(x)= -13.1239
The acquisition function optimization resulted in: 
     x:  [[  0.38115268  -0.58242051   0.15684818   1.81012335  -0.19986903
   -0.52916773   0.47053809  -1.56016015   2.15132534  -2.03411689
   -0.22366288  -1.33092479  -2.17876109  -2.44452932 -16.4134363
  -21.63311965 -22.83641781 -20.43637299 -32.47455082  -1.83841224
  -26.48162076]]
  f(x):  [-13.12385571]
acquisition funciton optimization tolerance changed to:  1.3123855708688499
Next points to be requested: 
[[  0.38115268  -0.58242051   0.15684818   1.81012335  -0.19986903
   -0.52916773   0.47053809  -1.56016015   2.15132534  -2.03411689
   -0.22366288  -1.33092479  -2.17876109  -2.44452932 -16.4134363
  -21.63311965 -22.83641781 -20.43637299 -32.47455082  -1.83841224
  -26.48162076]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++++

The acquisition function optimization resulted in: 
     x:  [[ 4.83258115e-01 -8.13023098e-01 -2.53055432e-02  1.17078725e+00
   7.18702058e-01 -8.84631016e-01 -1.89992510e-01 -2.52291533e+00
  -7.34179635e-01  1.93727005e+00 -3.86467964e+00  3.93908860e-01
  -1.31514220e-01  7.23656814e-01  4.39878706e+01 -2.12272352e+01
   1.76895000e+01  1.59512111e+01 -2.15239687e+01 -1.75719780e+01
  -2.44432999e+01]]
  f(x):  [-12.09947656]
acquisition funciton optimization tolerance changed to:  1.2099476564899112
Next points to be requested: 
[[ 4.83258115e-01 -8.13023098e-01 -2.53055432e-02  1.17078725e+00
   7.18702058e-01 -8.84631016e-01 -1.89992510e-01 -2.52291533e+00
  -7.34179635e-01  1.93727005e+00 -3.86467964e+00  3.93908860e-01
  -1.31514220e-01  7.23656814e-01  4.39878706e+01 -2.12272352e+01
   1.76895000e+01  1.59512111e+01 -2.15239687e+01 -1.75719780e+01
  -2.44432999e+01]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to 

differential_evolution step 1: f(x)= -12.9461
The acquisition function optimization resulted in: 
     x:  [[ -0.63492481  -0.80627712  -0.42898033   1.56484076   0.35339195
   -0.22769214   0.31264267  -1.81451337  -0.1459155    0.05212697
   -3.74821296   0.92606952   1.61107626   0.77921502 -45.10244662
   22.82547042  25.71100449  17.89225118 -38.03000449   6.75365147
  -23.12925698]]
  f(x):  [-12.94607321]
acquisition funciton optimization tolerance changed to:  1.2946073210126945
Next points to be requested: 
[[ -0.63492481  -0.80627712  -0.42898033   1.56484076   0.35339195
   -0.22769214   0.31264267  -1.81451337  -0.1459155    0.05212697
   -3.74821296   0.92606952   1.61107626   0.77921502 -45.10244662
   22.82547042  25.71100449  17.89225118 -38.03000449   6.75365147
  -23.12925698]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
+++++++++

## Plotting the 0th task in a 2d slice

In [20]:
x_pred = np.zeros((10000,21))
x = np.linspace(input_s[0,0],input_s[0,1],100)
y = np.linspace(input_s[1,0],input_s[1,1],100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.zeros((21))
        x_pred[counter,[0,1]] = np.array([x[i,j],y[i,j]])
        counter += 1
res = my_fvae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f)

## Back to a single task: using the GPOptimizer class directly gives you some more flexibility
We will show more soon!

In [21]:
#/usr/bin/env python
import numpy as np
from gpcam.gp_optimizer import GPOptimizer

#initialize some data
x_data = np.random.uniform(size = (100,1))
y_data = np.sin(x_data)[:,0]


#initialize the GPOptimizer
my_gpo = GPOptimizer(1,np.array([[0,1]]))
#tell() it some data
my_gpo.tell(x_data,y_data)
#initialize a GP ...
my_gpo.init_gp(np.ones(2))
#and train it
my_gpo.train_gp(np.array([[0.001,100],[0.001,100]]))

#let's make a prediction
print(my_gpo.posterior_mean(np.array([0.44])))

#now we can ask for a new point
r = my_gpo.ask()
print(r)
#putting the ask() in a loop and updating the data will
#give you all you need for your autonomous experiment

New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
fvGP training started with  100  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1.]  with old log likelihood:  -96.41897526173172
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  120
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= -159.821
differential_evolution step 2: f(x)= -159.821
differential_evolution step 3: f(x)= -159.821
differential_evolution step 4: f(x)= -161.729
differential_evolution step 5: f(x)= -161.729
differential_evolution step 6: f(x)= -161.752
differential_evolution step 7: f(x)= -161.752
differential_evolution step 8: f(x)= -161.936
differential_evolution step 9: f(x)= -162.188
differential_evolution step 10: f(x)= 